In [2]:
import face_recognition
import cv2
from sklearn.cluster import DBSCAN
import numpy as np
import os
import pickle
import signal
import sys
import math
import time
import random
from matplotlib import pyplot as plt
%matplotlib inline
from bokeh.plotting import figure
from bokeh.io import output_notebook, show, push_notebook


In [3]:

output_notebook()


def imshow(tit, image) :
    plt.title(tit)    
    if len(image.shape) == 3 :
        plt.imshow(cv2.cvtColor(image, cv2.COLOR_BGR2RGB))
    else :
        plt.imshow(image, cmap="gray")
    plt.show()
    
    
def create_win(frames, scale=1.0) :    
    global myImage
    
    all = []
    for f in frames :
        if len(f.shape ) !=  3 : f = cv2.cvtColor(f, cv2.COLOR_GRAY2BGR)
        all.append(f)
    frame = np.vstack(all)
    
    fr=cv2.cvtColor(frame, cv2.COLOR_BGR2RGBA) # because Bokeh expects a RGBA image
    fr=cv2.flip(fr, -1) # because Bokeh flips vertically
    width=fr.shape[1]
    height=fr.shape[0]    

    p = figure(x_range=(0,width), y_range=(0,height), output_backend="webgl", width=int(width*scale), height=int(height*scale))    
    myImage = p.image_rgba(image=[fr], x=0, y=0, dw=width, dh=height)
    show(p, notebook_handle=True)   
    
    
def update_win(frames) :
    
    all = []
    for f in frames :
        if len(f.shape ) !=  3 : f = cv2.cvtColor(f, cv2.COLOR_GRAY2BGR)
        all.append(f)
    frame = np.vstack(all)
    
    fr=cv2.cvtColor(frame, cv2.COLOR_BGR2RGBA)
    fr=cv2.flip(fr, -1)
    myImage.data_source.data['image']=[fr]
    push_notebook()


Loading BokehJS ...

In [4]:
src = cv2.VideoCapture('C:/Users/82107/Desktop/n_TIL/movie.mp4')
faces = []
frame_id = 0
frame_rate = src.get(5)
stop_at_frame = int(0 * frame_rate)
print("start encoding from src: %dx%d, %f frame/sec" % (src.get(3), src.get(4), frame_rate))


start encoding from src: 1280x720, 23.976024 frame/sec


In [5]:
known_face_encodings = []
known_face_names = []

In [6]:
dirname = 'knowns'
files = os.listdir(dirname)
for filename in files:
    name, ext = os.path.splitext(filename)
    if ext == '.png':
        known_face_names.append(name)
        pathname = os.path.join(dirname, filename)
        img = face_recognition.load_image_file(pathname)
        face_encoding = face_recognition.face_encodings(img)[0]
        known_face_encodings.append(face_encoding)

In [7]:
print(known_face_names)

['lee', 'ra']


In [8]:
face_locations = []
face_encodings = []
face_names = []
process_this_frame = True

In [9]:
for i in range(100):
    
    ret, frame = src.read()
    if i==0:
        create_win([frame], scale=0.5) 
    if not ret:
        break
        
    rgb_small_frame = frame[:, :, ::-1]
    
    face_locations = face_recognition.face_locations(rgb_small_frame ,model="hog")
    face_encodings = face_recognition.face_encodings(rgb_small_frame, face_locations)
    
    face_names = []
    for face_encoding in face_encodings:
        distances = face_recognition.face_distance(known_face_encodings,face_encoding)
        min_value = min(distances)

        name = "Unknown"
        if min_value < 0.6:
            index = np.argmin(distances)
            name = known_face_names[index]
        face_names.append(name)
    
    for (top, right, bottom, left), name in zip(face_locations, face_names):
    
    # Scale back up face locations since the frame we detected in was scaled to 1/4 size
        top *= 4
        right *= 4
        bottom *= 4
        left *= 4

        # Draw a box around the face
        cv2.rectangle(frame, (left, top), (right, bottom), (0, 0, 255), 2)

        # Draw a label with a name below the face
        cv2.rectangle(frame, (left, bottom - 35), (right, bottom), (0, 0, 255), cv2.FILLED)
        font = cv2.FONT_HERSHEY_DUPLEX
        cv2.putText(frame, name, (left + 6, bottom - 6), font, 1.0, (255, 255, 255), 1)
    update_win([frame])

